In [ ]:
#Weather Analysis in Colab and BigQuery Install Latest Version of Some Packages
!pip install --upgrade chart_studio

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.4/64.4 kB 1.6 MB/s eta 0:00:00


In [ ]:
#Weather Analysis in Colab and BigQuery Import Python Libraries & Some Other Setup
# Basic Python data science libraries
import pandas as pd
import numpy as np
import scipy.optimize

# setup and import for plotly in Colab
import chart_studio
import chart_studio.plotly as py
import plotly.graph_objects as go
import plotly.io as pio
import plotly.express as px

# enable displaying pandas data frames as interactive tables by default
from google.colab import data_table
data_table.enable_dataframe_formatter()

In [ ]:
# Weather Analysis in Colab and BigQuery Providing Google Creds to Colab Runtime (I think I will have to manually enter them)
from google.colab import auth
auth.authenticate_user()
print('Authenticated')

Authenticated


In [ ]:
# Weather Analysis in Colab and BigQuery Google Cloud/BigQuery Project ID
project_id = 'focused-mote-472706-u8' #@param{type:"string"}

# Package used for interfacing w/ BigQuery from Python
from google.cloud import bigquery

# Create BigQuery client
bq_client = bigquery.Client(project = project_id)

In [ ]:
#Weather Analysis in Colab with 2022 temp data from big query
project_id = 'focused-mote-472706-u8'

gsod_table = "`bigquery-public-data.noaa_gsod.gsod2022`"
stations_table = "`bigquery-public-data.noaa_gsod.stations`"


query = f"""
/* subquery which will count the number of dates with valid temperature data by station */
WITH
Num2022TempDatesByStation as
( SELECT
  daily_weather.stn,
    COUNT(DISTINCT
      DATE(
        CAST(daily_weather.year AS INT64)
        , CAST(daily_weather.mo as INT64)
        , CAST(daily_weather.da as INT64)
      )) AS num_22_temp_dates

  FROM {gsod_table} as daily_weather

  WHERE daily_weather.temp IS NOT NULL
  AND
  daily_weather.max IS NOT NULL
  AND
  daily_weather.min IS NOT NULL
  # removing days with missing temps (999999.9)
  AND
  daily_weather.temp != 9999.9
  AND
  daily_weather.max != 9999.9
  AND
  daily_weather.min != 9999.9

  GROUP BY
  daily_weather.stn
),

# finding the max number of high temp dates in 2022 across all stations

MaxNum2022TempDates AS

(
  SELECT
  MAX(num_22_temp_dates) AS max_num_22_temp_dates

  FROM Num2022TempDatesByStation
)

SELECT
  Stations.*,
  Num2022TempDatesByStation.num_22_temp_dates

FROM
  {stations_table} Stations

# Inner join to filter to only stations present in 2022 data */
INNER JOIN
  Num2022TempDatesByStation ON (
    stations.usaf = Num2022TempDatesByStation.stn
    )

# Cross join to get max number on each row, to use in filtering below */
CROSS JOIN
  MaxNum2022TempDates


WHERE
  # Take out stations w/ USAF # 999999 (appear to be older ones) */
  Stations.usaf != '999999' AND
  # Keep stations that started tracking 1/1/2000 or earlier */
  Stations.begin <= '20000101' AND
  # Keep stations that tracked through at least 12/31/2020 */
  Stations.end >= '20201231' AND
  # Filter to stations w/ >= 90% of the max number of dates for 2022 */
  Num2022TempDatesByStation.num_22_temp_dates >=
    (0.90 * MaxNum2022TempDates.max_num_22_temp_dates)

ORDER BY
  stations.usaf
"""

%%bigquery weather_stations --project $project_id -q $query

UsageError: Line magic function `%%bigquery` not found.


In [ ]:
#Weather Analysis in Colab with 2022 temp data from big query
%%bigquery weather_stations --project {project_id}

WITH
Num2022TempDatesByStation AS
(
  SELECT
    daily_weather.stn,

    /* Count # of distinct dates w/ temperature data for each station */
    COUNT(DISTINCT
      /* Convert year/month/day info into date */
      DATE(
        CAST(daily_weather.year AS INT64),
        CAST(daily_weather.mo AS INT64),
        CAST(daily_weather.da AS INT64)
        )) AS num_2022_temp_dates

  FROM
    `bigquery-public-data.noaa_gsod.gsod2022` daily_weather

  WHERE
    daily_weather.temp IS NOT NULL AND
    daily_weather.max IS NOT NULL AND
    daily_weather.min IS NOT NULL AND
    # Remove days w/ missing temps coded as 99999.9
    daily_weather.temp != 9999.9 AND
    daily_weather.max != 9999.9 AND
    daily_weather.min != 9999.9

  GROUP BY
    daily_weather.stn
),

# Calculate max number of 2022 temperature dates across all stations
MaxNum2022TempDates AS
(
  SELECT
    MAX(num_2022_temp_dates) AS max_num_2022_temp_dates

  FROM
    Num2022TempDatesByStation
)

SELECT
  Stations.*,
  Num2022TempDatesByStation.num_2022_temp_dates

FROM
  `bigquery-public-data.noaa_gsod.stations` Stations

# Inner join to filter to only stations present in 2022 data
INNER JOIN
  Num2022TempDatesByStation ON (
    stations.usaf = Num2022TempDatesByStation.stn
    )

# Cross join to get max number on each row, to use in filtering below
CROSS JOIN
  MaxNum2022TempDates

WHERE
  # Take out stations w/ USAF # 999999 (appear to be older ones)
  Stations.usaf != '999999' AND
  # Keep stations that started tracking 1/1/2000 or earlier
  Stations.begin <= '20000101' AND
  # Keep stations that tracked through at least 12/31/2020 */
  Stations.end >= '20201231' AND
  # Filter to stations w/ >= 90% of the max number of dates for 2022 */
  Num2022TempDatesByStation.num_2022_temp_dates >=
    (0.90 * MaxNum2022TempDates.max_num_2022_temp_dates)

ORDER BY
  stations.usaf

Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
# Load the BigQuery magic command
%load_ext google.colab.sql

The google.colab.sql module is not an IPython extension.


In [ ]:
# Interactive Table of Weather Stations
weather_stations

usaf   wban                   name country state  call     lat  \
0     010080  99999               LONGYEAR      SV  None  ENSB  78.246   
1     010100  99999                 ANDOYA      NO  None  ENAN  69.293   
2     010230  99999              BARDUFOSS      NO  None  ENDU  69.056   
3     010250  99999                 TROMSO      NO  None  ENTC  69.683   
4     010460  99999              SORKJOSEN      NO  None  ENSR  69.787   
...      ...    ...                    ...     ...   ...   ...     ...   
6177  994390  99999  SETTLEMENT POINT  GBI      US  None  None  26.700   
6178  994400  99999       THOMAS POINT  MD      US  None  None  38.900   
6179  994410  99999      ST. AUGUSTINE  FL      US  None  None  29.860   
6180  994450  99999       SOMBRERO KEY  FL      US    FL  None  24.630   
6181  994560  99999        FOWEY ROCKS  FL      US  None  None  25.590   

         lon     elev     begin       end  num_2022_temp_dates  
0     15.466  +0026.8  19750929  20210920                  365  
1     16.144  +0013.1  19310103  20210920                  364  
2     18.540  +0076.8  19400713  20210920                  365  
3     18.919  +0009.4  19730101  20210920                  365  
4     20.959  +0004.9  19750905  20210920                  352  
...      ...      ...       ...       ...                  ...  
6177 -79.000  +0001.5  19851203  20210920                  365  
6178 -76.440  +0000.0  19851205  20210920                  365  
6179 -81.260  +0000.0  19870122  20210920                  365  
6180 -81.110  +0000.0  19880929  20210920                  365  
6181 -80.100  +0000.0  19940901  20210920                  341  

[6182 rows x 12 columns]

In [ ]:
#figuring out usaf number with bigquery

%%bigquery catalina_usaf_result --project {project_id}
SELECT usaf
FROM `bigquery-public-data.noaa_gsod.stations`
WHERE name = 'CATALINA AIRPORT (US)'

Query is running:   0%|          |

Downloading: |          |

In [ ]:
print(catalina_usaf_result['usaf'].iloc[0])

IndexError: single positional indexer is out-of-bounds

In [ ]:
## Interactive Map of Weather Stations Throughout the World
weather_stations['display_feild'] = weather_stations.apply(lambda row:
                                                          f"{row['name']} ({row['country']})",
                                                          axis = 1)
fig = px.scatter_geo(weather_stations, lat = 'lat', lon = 'lon',
                     hover_name = 'display_feild')

fig.show()

In [ ]:
import plotly.express as px

In [ ]:
# Chosing a weather station by USAF
chosen_station_usaf = '722920' #Catalina Island Airport

if chosen_station_usaf not in weather_stations['usaf'].tolist():
  print('Not a Valid USAF, Picking Random Weather Station Instead...')
  chosen_station_usaf = weather_stations['usaf'].sample(1).iloc[0]

# Filter to only chosen station
chosen_station_info = weather_stations[weather_stations['usaf'] ==
  chosen_station_usaf]

  chosen_station_name = chosen_station_info['name'].iloc[0]

  # adding a station to usaf BigQuery paramaters
  bigquery_params = {
      'chosen_station_usaf': chosen_station_usaf
  }

print(f'Chosen Station: {chosen_station_name}')
chosen_station_info

IndentationError: unexpected indent (ipython-input-2586054401.py, line 12)

In [ ]:
chosen_station_usaf = "722920" #Catalina Island Airport usaf

if chosen_station_usaf not in weather_stations['usaf'].tolist():
  print('Not a Valid USAF, Picking Random Weather Station Instead...')
  chosen_station_usaf = weather_stations['usaf'].sample(1).iloc[0]

# Filter to only chosen station
chosen_station_info = weather_stations[weather_stations['usaf'] ==
  chosen_station_usaf]

chosen_station_name = chosen_station_info['name'].iloc[0]

# Add station usaf to BigQuery parameters dictionary
bigquery_params = {
  "chosen_station_usaf": chosen_station_usaf
  }

print(f'Chosen Station: {chosen_station_name}')
chosen_station_info

Chosen Station: CATALINA AIRPORT


usaf   wban              name country state  call     lat      lon  \
4699  722920  23191  CATALINA AIRPORT      US    CA  KAVX  33.405 -118.416   

         elev     begin       end  num_2022_temp_dates          display_feild  
4699  +0488.3  19430612  20210921                  352  CATALINA AIRPORT (US)

In [ ]:
# getting Daily Temperature Data for Chosen Station (for just one year)
%%bigquery chosen_station_daily_2022 --project {project_id} --params $bigquery_params

SELECT
  # Station information
  daily_weather.stn AS usaf

  , DATE( #converting year/month/day info into date
      CAST(daily_weather.year AS INT64)
      , CAST(daily_weather.mo AS INT64)
      , CAST(daily_weather.da AS INT64)
      ) AS date

    , daily_weather.temp AS avg_temp
    , daily_weather.count_temp AS n_for_avg_temp

    , daily_weather.max AS max_temp

    , daily_weather.min AS min_temp


FROM `bigquery-public-data.noaa_gsod.gsod2022` daily_weather

WHERE
0=0
AND
daily_weather.stn = @chosen_station_usaf #Filtering to only chosen station
AND
daily_weather.temp != 9999.9
AND
daily_weather.max != 9999.9
AND
daily_weather.min != 9999.9

ORDER BY
  date DESC

Query is running:   0%|          |

Downloading:   0%|          |

In [ ]:
chosen_station_daily_2022

usaf        date  avg_temp  n_for_avg_temp  max_temp  min_temp
0    722920  2022-12-31      54.2              24      55.9      51.1
1    722920  2022-12-30      52.5              24      55.0      51.1
2    722920  2022-12-29      50.8              24      54.0      48.2
3    722920  2022-12-28      53.0              24      69.1      51.1
4    722920  2022-12-27      63.1              24      78.1      53.1
..      ...         ...       ...             ...       ...       ...
347  722920  2022-01-05      56.6              24      64.9      44.1
348  722920  2022-01-04      49.4              24      57.9      44.1
349  722920  2022-01-03      50.6              24      57.9      44.1
350  722920  2022-01-02      50.3              24      57.9      44.1
351  722920  2022-01-01      48.7              24      54.0      44.6

[352 rows x 6 columns]

In [ ]:
# Plotting Daily Temp Data for Chosen Stations (2022)
# Create table of temperature series to plot, with names, symbols, colors
daily_temp_plot_fields = pd.DataFrame.from_records(
  columns = ['field_name', 'plot_label', 'marker_symbol', 'line_color',
    'plot_mode'],
  data = [
    ('avg_temp', 'Avg', 'circle', None, 'markers')
    , ('max_temp', 'Max', 'triangle-up', None, 'markers')
    , ('min_temp', 'Min', 'triangle-down', None, 'markers')
    ]
  )

# Create function to plot single station daily temperature
def plot_single_station_daily_temp(daily_temp_data, plot_fields, station_name):
  daily_plot_data = []

  for index, row in plot_fields.iterrows():
    daily_plot_data = (daily_plot_data +
      [go.Scatter(
        x = daily_temp_data['date'],
        y = daily_temp_data[row['field_name']],
        name = row['plot_label'],
        marker = dict(
          # Constant color scale for plotting temp to use for all stations
          cmin = -22, # -22°F corresponds to -30°C (very cold, to most)
          cmax = 122, # 122°F corresponds to 50°C (very hot, to most)
          color = daily_temp_data[row['field_name']],
          # colorscale = 'BlueReds',
          colorscale = [[0, 'rgb(0, 0, 230)'], [0.5, 'rgb(190, 190, 190)'],
            [1, 'rgb(230, 0, 0)']],
          symbol = row['marker_symbol']
          ),
        line = dict(
          color = row['line_color']
          ),
        mode = row['plot_mode']
        )]
      )

  daily_plot_layout = go.Layout(
    title = dict(
      text = f'{station_name} Daily Temperature',
      xref = "paper",
      x = 0.5
      ),
    yaxis = dict(title = 'Temperature (°F)')
    )

  pio.show(go.Figure(daily_plot_data, daily_plot_layout))

plot_single_station_daily_temp(chosen_station_daily_2022,
  daily_temp_plot_fields, chosen_station_name)

In [ ]:
# Get and Plot Munti_Year Daily Temp Data for Catalina

chosen_start_year = 2005

chosen_end_year = 2025 # not sure if 25 works, if not revert to 2022

def get_single_station_daily_temp_multiple_yrs(station_usaf, start_year,
  end_year):

  single_station_daily_multiyear_sql = f'''
    SELECT
      daily_weather.stn AS usaf,

      /* Convert year/month/day info into date */
      DATE(
        CAST(daily_weather.year AS INT64),
        CAST(daily_weather.mo AS INT64),
        CAST(daily_weather.da AS INT64)
        ) AS date,

      daily_weather.temp AS avg_temp,
      daily_weather.count_temp AS n_for_avg_temp,

      daily_weather.max AS max_temp,
      daily_weather.flag_max AS max_temp_flag,

      daily_weather.min AS min_temp,
      daily_weather.flag_min AS min_temp_flag

    FROM
      `bigquery-public-data.noaa_gsod.gsod*` daily_weather

    WHERE
      /* Filter to only chosen station */
      daily_weather.stn = '{station_usaf}' AND
      /* Filter to only chosen years */
      _table_suffix BETWEEN '{start_year}' AND '{end_year}' AND # Using _table_suffix for year filtering
      /* Remove days w/ missing temps coded as 99999.9 (can throw off calcs) */
      daily_weather.temp != 9999.9 AND
      daily_weather.max != 9999.9 AND
      daily_weather.min != 9999.9

    ORDER BY
      date DESC
    '''

  single_station_daily_multiyear_df = (bq_client.
    query(single_station_daily_multiyear_sql).
    result().
    to_arrow().
    to_pandas()
    )

  # Convert 'date' column to datetime objects
  single_station_daily_multiyear_df['date'] = pd.to_datetime(single_station_daily_multiyear_df['date'])


  return(single_station_daily_multiyear_df)

chosen_station_daily_multiyear = get_single_station_daily_temp_multiple_yrs(
  chosen_station_usaf, chosen_start_year, chosen_end_year
  )

plot_single_station_daily_temp(chosen_station_daily_multiyear,
  daily_temp_plot_fields, chosen_station_name)

In [ ]:
# Title Functions to fit the sine curve to daily multi year temp data

# describe the sunusoidal model as function w/ parameters if interest
def sin_function(t, amp, freq, phase_shift, mean):
  return (amp * np.sin(freq * 2 * np.pi * (t - phase_shift)) + mean)

#fitting the simusoidal model to data, which should return either fit info or daily temp estimates
def fit_sine_curve_to_daily_temp_data(daily_temp_data, temp_field_name,
  return_value = 'sine curve fit info'):

  # Calculating the total range of days in data
  daily_temp_data['data_since_start'] = (daily_temp_data['date'] -
                                         min(daily_temp_data['date'])).dt.days

  # Starting point for mean is mean of temp
  guess_mean = daily_temp_data[temp_field_name].mean()

  #Starting point for amplitude is half the dif between 1st and 99th %tiles of temp
  guess_amp = (daily_temp_data[temp_field_name].quantile(0.99) -
               daily_temp_data[temp_field_name].quantile(0.01)) / 2
  # Starting point for frequency is inverse of avg # of days in year
  guess_freq = 1/365.25

  # Starting Point for phase shift is +80 days into spring (typically)
  guess_phase_shift = 80

  # using curve shift optimizer on data with above guesses as the start point
  sine_curve_fit = scipy.optimize.curve_fit(
      f = sin_function,
      xdata = np.array(daily_temp_data['data_since_start']),
      ydata = np.array(daily_temp_data[temp_field_name]),
      p0 = [guess_amp, guess_freq, guess_phase_shift, guess_mean]
  )

  #extract estimated parameters from curve fit
  est_amp, est_freq, est_phase_shift, est_mean = sine_curve_fit[0]

  #use the sine function and params to get the daily estimates of avg temp
  daily_temp_data[f'est_{temp_field_name}'] = sin_function(
      daily_temp_data['data_since_start'],
      est_amp, est_freq, est_phase_shift, est_mean
  )

  #calculate mean absolute error of estimates vs actual temp
  curve_estimate_mean_abs_err = abs(
      daily_temp_data[f'est_{temp_field_name}'] - daily_temp_data[temp_field_name]
  ).mean()

  #creating the data frame of the sine curve
  sine_curve_fit_info_df = pd.DataFrame(data = [{
      f'est_amp_{temp_field_name}': est_amp,
      f'est_freq_{temp_field_name}': est_freq,
      f'est_phase_shift_{temp_field_name}': est_phase_shift,
      f'est_mean_{temp_field_name}': est_mean,
      f'est_range_{temp_field_name}': 2 * abs(est_amp),
      f'mae_fitted_{temp_field_name}': curve_estimate_mean_abs_err
      }])

  # retune either sine curve fit into or daily temp data
  if(return_value == 'sine curve fit info'):
    return(sine_curve_fit_info_df)

  elif(return_value == 'daily temp data with estimates'):
    return(daily_temp_data)

In [ ]:
# Plotting Daily Temp Data for Chosen Stations (Multi-Year) with Sine Curve Fit
def plot_single_station_daily_temp_with_fit(daily_temp_data, plot_fields, station_name):
  daily_plot_data = []

  for index, row in plot_fields.iterrows():
    # Add actual temperature data points
    daily_plot_data.append(
        go.Scatter(
            x=daily_temp_data['date'],
            y=daily_temp_data[row['field_name']],
            name=f"{row['plot_label']} (Actual)",
            mode=row['plot_mode'],
            marker=dict(
                cmin=-22,
                cmax=122,
                color=daily_temp_data[row['field_name']],
                colorscale=[[0, 'rgb(0, 0, 230)'], [0.5, 'rgb(190, 190, 190)'], [1, 'rgb(230, 0, 0)']],
                symbol=row['marker_symbol']
            )
        )
    )

    # Add fitted sine curve line ONLY for avg_temp (as it's the only one fitted)
    if row['field_name'] == 'avg_temp':
        daily_plot_data.append(
            go.Scatter(
                x=daily_temp_data['date'],
                y=daily_temp_data[f'est_{row["field_name"]}'],
                name=f"{row['plot_label']} (Fitted Sine Curve)",
                mode='lines',
                line=dict(color='black', dash='dash') # Use a distinct style for the fitted line
            )
        )


  daily_plot_layout = go.Layout(
    title = dict(
      text = f'{station_name} Daily Temperature with Sine Curve Fit ({min(daily_temp_data["date"]).year}-{max(daily_temp_data["date"]).year})',
      xref = "paper",
      x = 0.5
      ),
    yaxis = dict(title = 'Temperature (°F)'),
    xaxis = dict(title = 'Date')
    )

  pio.show(go.Figure(daily_plot_data, daily_plot_layout))

# Use the plotting function with the multi-year data and estimates
plot_single_station_daily_temp_with_fit(chosen_station_daily_multiyear_with_estimates,
                                        daily_temp_plot_fields,
                                        chosen_station_name)

In [ ]:
# Convert 'date' column to datetime objects
chosen_station_daily_multiyear['date'] = pd.to_datetime(chosen_station_daily_multiyear['date'])

# Fit sine curve to multi-year daily average temperature data
chosen_station_daily_multiyear_with_estimates = fit_sine_curve_to_daily_temp_data(
    chosen_station_daily_multiyear,
    'avg_temp',
    return_value = 'daily temp data with estimates'
)

# Display the daily data with the fitted sine curve estimates
display(chosen_station_daily_multiyear_with_estimates.head())

# Get and display the sine curve fit information
sine_curve_fit_info = fit_sine_curve_to_daily_temp_data(
    chosen_station_daily_multiyear,
    'avg_temp',
    return_value = 'sine curve fit info'
)

print("\nSine curve fit information:")
display(sine_curve_fit_info)

usaf       date  avg_temp  n_for_avg_temp  max_temp max_temp_flag  \
0  722920 2025-08-27      64.9               8      72.0             *   
1  722920 2025-08-26      66.6              24      73.0             *   
2  722920 2025-08-25      76.5              24      84.0             *   
3  722920 2025-08-24      79.2              24      93.0          None   
4  722920 2025-08-23      79.4              24      93.0          None   

   min_temp min_temp_flag  data_since_start  est_avg_temp  
0      59.0             *              7543     69.548774  
1      60.1             *              7542     69.553919  
2      72.0             *              7541     69.556698  
3      70.0          None              7540     69.557108  
4      70.0          None              7539     69.555150


Sine curve fit information:


est_amp_avg_temp  est_freq_avg_temp  est_phase_shift_avg_temp  \
0          8.011744           0.002736                140.201394   

   est_mean_avg_temp  est_range_avg_temp  mae_fitted_avg_temp  
0           61.54549           16.023488             6.495338

In [ ]:
chosen_station_daily_temp_with_preds = fit_sine_curve_to_daily_temp_data(
  daily_temp_data = chosen_station_daily_multiyear,
  temp_field_name = 'avg_temp',
  return_value = 'daily temp data with estimates'
  )

# Set up plot fields structure: points for actual temp, curve for estimated temp
daily_avg_and_estimate_plot_fields = pd.DataFrame.from_records(
  columns = ['field_name', 'plot_label', 'marker_symbol', 'line_color',
    'plot_mode'],
  data = [
    ('avg_temp', 'Actual Avg', 'circle', None, 'markers'),
    ('est_avg_temp', 'Estimated Avg', None, 'purple', 'lines')
    ]
  )

# Use function to plot daily temperature with estimates for given station
plot_single_station_daily_temp(chosen_station_daily_temp_with_preds,
  daily_avg_and_estimate_plot_fields, chosen_station_name)

In [ ]:
# Choose number of weather stations to sample (randomly) from above list
num_stations_to_sample = 10 #@param {type:"number"}

# Enter USAF #s of other weather stations to be included (quoted & separated by commas)
other_usafs_to_include = "['722920', '825910', '890090', '974060']" #@param {type:"string"}

# Seed for random # generation to ensure consistent sampling (reproducibility)
seed = 23

chosen_weather_stations = pd.concat([
  # Randomly sample specified number of weather stations
  weather_stations.sample(
    # Cap # of stations sampled at # in dataset to avoid errors
    n = min(weather_stations.shape[0], num_stations_to_sample),
    random_state = seed
    ),
  # Filter to other specified stations provided in array of USAFs
  weather_stations.query(f'usaf in {other_usafs_to_include}')
  ],
  ignore_index = True
  # Might be duplicates if sampled & fixed stations overlap, so drop them
  ).drop_duplicates()

# Initialize list of sine curve fit info data frames
sine_curve_fit_info_df_collection = []

# Loop over data frame of chosen weather stations
for index, row in chosen_weather_stations.iterrows():
  # Use function to get daily temperature data for given station from BigQuery
  this_station_daily_temp_data = get_single_station_daily_temp_multiple_yrs(
    station_usaf = row['usaf'],
    start_year = chosen_start_year,
    end_year = chosen_end_year
    )

  # Don't count unless station has >=500 days of temperature data
  if(this_station_daily_temp_data.shape[0] < 500):
    # Print message and move on in this case
    print(f"Not Enough Temp Data for USAF {row['usaf']} {row['name']}")

  # As long as station has >=500 days of temperature data
  else:
    # Ensure the 'date' column is datetime before fitting
    this_station_daily_temp_data['date'] = pd.to_datetime(this_station_daily_temp_data['date'])

    # Use function to find sine curve fit for this station's temperature data
    this_station_temp_sine_curve_fit_info = fit_sine_curve_to_daily_temp_data(
      daily_temp_data = this_station_daily_temp_data,
      temp_field_name = 'avg_temp'
      )

    # Add station USAF and name to this fit into data frame
    this_station_temp_sine_curve_fit_info['station_usaf'] = row['usaf']
    this_station_temp_sine_curve_fit_info['station_name'] = row['name']

    # Add data frame for this station to collection for all stations
    sine_curve_fit_info_df_collection = (sine_curve_fit_info_df_collection +
      [this_station_temp_sine_curve_fit_info])

# Concatenate collection of all stations' data frames into 1 data frame
all_station_fit_info = pd.concat(sine_curve_fit_info_df_collection,
  ignore_index = True).set_index(['station_usaf', 'station_name']).reset_index()

# Look at interactive table of all station fit info
all_station_fit_info

station_usaf          station_name  est_amp_avg_temp  est_freq_avg_temp  \
0        946140            SWANBOURNE         -9.157496           0.002738   
1        161220               ALBENGA         15.889382           0.002737   
2        476000                WAJIMA         20.577998           0.002739   
3        289000              KURUMOCH         30.039749           0.002739   
4        684950  RICHARDS BAY AIRPORT          6.176235           0.002741   
5        942160             KUNUNURRA         -7.184531           0.002738   
6        405850              SALMIYAH         20.530437           0.002737   
7        024180              KARLSTAD         17.781804           0.002740   
8        604250           ECH CHELIFF         17.658422           0.002739   
9        234180               PECHORA         29.087364           0.002739   
10       722920      CATALINA AIRPORT          8.011744           0.002736   
11       825910       DIX SEPT ROSADO          1.381047           0.002742   
12       890090        AMUNDSEN-SCOTT        -27.377201           0.002738   
13       974060    GALELA/GAMARMALAMU          0.204171           0.003014   

    est_phase_shift_avg_temp  est_mean_avg_temp  est_range_avg_temp  \
0                 119.244402          65.434090           18.314992   
1                 110.903674          63.165447           31.778765   
2                 122.400600          57.430085           41.155996   
3                 106.943714          43.167902           60.079499   
4                   3.863489          71.312300           12.352471   
5                  84.504920          81.321365           14.369061   
6                  87.110159          80.162848           41.060874   
7                 111.793555          44.335965           35.563609   
8                  85.882454          68.665792           35.316845   
9                 110.424646          31.092040           58.174728   
10                140.201394          61.545490           16.023488   
11                108.807944          88.902384            2.762095   
12                 87.703112         -55.585911           54.754402   
13                307.788304          80.468572            0.408343   

    mae_fitted_avg_temp  
0              3.749698  
1              3.901068  
2              3.959458  
3              7.194384  
4              3.206435  
5              3.666349  
6              2.827253  
7              5.227919  
8              4.322926  
9              9.465838  
10             6.495338  
11             2.305029  
12            12.024919  
13             1.578650

In [ ]:
station_usaf = '722920'

# Message if station is not in our chosen set
if station_usaf not in chosen_weather_stations['usaf'].tolist():
  print('Not in Chosen Weather Stations')

# Message if station was in our chosen set, but not enough temperature data
elif station_usaf not in all_station_fit_info['station_usaf'].tolist():
  print(f'Not Enough Temp Data for USAF {station_usaf}')

else:
  # Filter to only chosen station
  station_fit_info = all_station_fit_info[
    all_station_fit_info['station_usaf'] == station_usaf]

  # Print fit into
  print(station_fit_info.round(decimals = 4))

  # Extract weather station name
  station_name = station_fit_info['station_name'].iloc[0]

  # Use function to get daily temperature data for given station from BigQuery
  station_daily_temp_data = get_single_station_daily_temp_multiple_yrs(
    station_usaf = station_usaf,
    start_year = chosen_start_year,
    end_year = chosen_end_year
    )

  # Use function to find sine curve fit for this station's temperature data
  station_daily_temp_data_with_preds = fit_sine_curve_to_daily_temp_data(
    daily_temp_data = station_daily_temp_data,
    temp_field_name = 'avg_temp',
    return_value = 'daily temp data with estimates'
    )

  # Use function to plot given station's daily temperature with model estimates
  plot_single_station_daily_temp(station_daily_temp_data_with_preds,
    daily_avg_and_estimate_plot_fields, station_name)

   station_usaf      station_name  est_amp_avg_temp  est_freq_avg_temp  \
10       722920  CATALINA AIRPORT            8.0117             0.0027   

    est_phase_shift_avg_temp  est_mean_avg_temp  est_range_avg_temp  \
10                  140.2014            61.5455             16.0235   

    mae_fitted_avg_temp  
10               6.4953  


In [ ]:
# All Weather Stations Data Table
output_dataset_id = 'weather_demo'

output_table_id = 'sample_station_temp_curve_fit_info'

replace_or_append_output = 'replace'

# Combine project and dataset
project_dataset = f"{bq_client.project}.{output_dataset_id}"

# Combine project, dataset, and table
project_dataset_table = f"{project_dataset}.{output_table_id}"

# Check to make sure output dataset exists, create it if not
try:
  bq_client.get_dataset(output_dataset_id)
  print(f"BigQuery dataset {project_dataset} exists\n")

except:
  print(f"BigQuery dataset {project_dataset} doesn't exist, so creating it\n")
  dataset = bq_client.create_dataset(bigquery.Dataset(project_dataset))

job_config = bigquery.LoadJobConfig()

# Modify job config depending on if we want to replace or append to table
if(replace_or_append_output == 'replace'):
  job_config.write_disposition = bigquery.WriteDisposition.WRITE_TRUNCATE
else:
  job_config.write_disposition = bigquery.WriteDisposition.WRITE_APPEND

dataset_ref = bq_client.dataset(output_dataset_id)
table_ref = dataset_ref.table(output_table_id)

# Get timestamp (UTC), add to data frame at granularity of seconds
all_station_fit_info['timestamp'] = pd.Timestamp.now(tz = 'UTC').ceil(freq = 's'
  )

# Use client functionality to load BigQuery table from Pandas data frame
bq_client.load_table_from_dataframe(
  dataframe = all_station_fit_info,
  destination = table_ref,
  job_config = job_config
  ).result()

print((f"Sample Station Fit Info output ({replace_or_append_output}) to "
  f"BigQuery table {project_dataset_table}\n"))

BigQuery dataset focused-mote-472706-u8.weather_demo doesn't exist, so creating it

Sample Station Fit Info output (replace) to BigQuery table focused-mote-472706-u8.weather_demo.sample_station_temp_curve_fit_info

